In [1]:
import shutil
import os

# # Create destination directory if it doesn't exist
# os.makedirs("/kaggle/working/", exist_ok=True)

# Copy the file
shutil.copy("/kaggle/input/anomalies-data/metric_backup.json", 
            "/kaggle/working/metric_backup.json")


'/kaggle/working/metric_backup.json'

## LSTM

In [2]:
import os
import json
import pickle
import gc
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Input
from tensorflow.keras.callbacks import EarlyStopping
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error
from datetime import datetime
from zoneinfo import ZoneInfo
from multiprocessing import Process, set_start_method

# -------------------- Configuration --------------------

METRIC_DATASET_PATH = "/kaggle/working/metric_backup.json"
MODEL_DIR = "/kaggle/working/saved_models"
VISUALS_DIR = "/kaggle/working/visuals"
ANOMALIES_JSON_PATH = "/kaggle/working/anomalies.json"

for folder in [MODEL_DIR, VISUALS_DIR]:
    os.makedirs(folder, exist_ok=True)

SEQUENCE_LENGTH = 30
EPOCHS = 60
BATCH_SIZE = 16
LATENT_DIM = 32
MIN_SAMPLES = 100
TRAIN_RATIO = 0.7
THRESHOLD_SIGMA = 6.0
TRENDING_SLOPE_THRESHOLD = 0.01

# Dictionary to store MSE scores
metric_mse_scores = {}
all_mse_values = []

try:
    set_start_method("spawn")
except RuntimeError:
    pass

# Load the dataset
df = pd.read_json(METRIC_DATASET_PATH, lines=True)
metrics = df["metric_name"].unique()
print(f"[INFO] Found {len(metrics)} unique metrics.")

# Process each metric
for metric in metrics:
    try:
        print(f"[INFO] Processing: {metric}")
        
        # Filter and sort data for the current metric
        metric_df = df[df["metric_name"] == metric].copy()
        metric_df["timestamp"] = pd.to_datetime(metric_df["timestamp"])
        metric_df.sort_values("timestamp", inplace=True)
        data = metric_df["value"].values.astype(float)
        timestamps = metric_df["timestamp"].values
        
        if len(data) == 0:
            print(f"[WARN] No data for '{metric}'. Skipping.")
            continue
            
        if len(data) < MIN_SAMPLES:
            print(f"[WARN] Not enough data for '{metric}' ({len(data)} < {MIN_SAMPLES}). Skipping.")
            continue
            
        # Check if the metric is trending
        x = np.arange(len(data))
        slope = np.polyfit(x, data, 1)[0]
        use_transformation = slope > TRENDING_SLOPE_THRESHOLD
        print(f"[INFO] '{metric}' {'trending' if use_transformation else 'not trending'} (slope={slope:.4f})")
        
        # Transform data if needed
        if use_transformation:
            # Calculate differences and clip negative values
            diff = np.diff(data, prepend=data[0])
            data = np.where(diff < 0, 0, diff)
        
        # Split into train and test sets
        split_idx = int(len(data) * TRAIN_RATIO)
        train_data, test_data = data[:split_idx], data[split_idx:]
        train_timestamps, test_timestamps = timestamps[:split_idx], timestamps[split_idx:]
        
        # Scale the data
        scaler = StandardScaler()
        train_scaled = scaler.fit_transform(train_data.reshape(-1, 1))
        
        # Create sequences for LSTM
        X_train, y_train = [], []
        for i in range(len(train_scaled) - SEQUENCE_LENGTH):
            X_train.append(train_scaled[i: i + SEQUENCE_LENGTH])
            y_train.append(train_scaled[i + SEQUENCE_LENGTH])
        X_train = np.array(X_train)
        y_train = np.array(y_train).reshape(-1, 1)
        
        # Build and train the model
        model = Sequential([
            Input(shape=(SEQUENCE_LENGTH, X_train.shape[-1])),
            LSTM(LATENT_DIM, activation="relu"),
            Dense(X_train.shape[-1])
        ])
        model.compile(optimizer="adam", loss="mae")
        
        early_stop = EarlyStopping(monitor="loss", patience=5, restore_best_weights=True)
        
        model.fit(
            X_train, y_train,
            epochs=EPOCHS,
            batch_size=BATCH_SIZE,
            validation_split=0.1,
            verbose=0,
            callbacks=[early_stop]
        )
        
        # Compute errors on training data
        y_pred_train = model.predict(X_train)
        errors = np.abs(y_train - y_pred_train).flatten()
        mean_err, std_err = np.mean(errors), np.std(errors)
        threshold = mean_err + THRESHOLD_SIGMA * std_err
        
        # Save model and related data
        model.save(os.path.join(MODEL_DIR, f"{metric}_forecast.keras"))
        with open(os.path.join(MODEL_DIR, f"{metric}_scaler.pkl"), "wb") as f:
            pickle.dump(scaler, f)
        with open(os.path.join(MODEL_DIR, f"{metric}_thresholds.pkl"), "wb") as f:
            pickle.dump({
                "threshold": threshold,
                "mean_error": float(mean_err),
                "std_error": float(std_err),
                "use_transformation": use_transformation
            }, f)
        
        # Detect anomalies in test data
        if use_transformation:
            diff = np.diff(test_data, prepend=test_data[0])
            test_data = np.where(diff < 0, 0, diff)
            
        test_scaled = scaler.transform(test_data.reshape(-1, 1))
        
        # Create sequences for test data
        X_test, y_test = [], []
        for i in range(len(test_scaled) - SEQUENCE_LENGTH):
            X_test.append(test_scaled[i: i + SEQUENCE_LENGTH])
            y_test.append(test_scaled[i + SEQUENCE_LENGTH])
        X_test = np.array(X_test)
        y_test = np.array(y_test).reshape(-1, 1)
        
        if len(X_test) == 0:
            print(f"[WARN] Insufficient sequence data for '{metric}'.")
            continue
            
        # Make predictions on test data
        y_pred = model.predict(X_test)
        
        # Calculate MSE for this metric
        mse = mean_squared_error(y_test, y_pred)
        metric_mse_scores[metric] = mse
        all_mse_values.append(mse)
        print(f"[INFO] MSE for {metric}: {mse:.6f}")
        
        # Calculate errors and find anomalies
        errors = np.abs(y_test - y_pred).flatten()
        flags = errors > threshold
        
        # Collect anomalies
        anomalies = []
        for i, flag in enumerate(flags):
            if flag:
                idx = i + SEQUENCE_LENGTH
                if idx < len(test_timestamps):
                    anomalies.append({
                        "timestamp": pd.to_datetime(test_timestamps[idx]).isoformat(),
                        "value": float(test_data[idx]),
                        "forecast_error": float(errors[i])
                    })
        
        # Print anomalies
        for a in anomalies:
            print(f"[ANOMALY] {metric} @ {a['timestamp']}: val={a['value']:.3f}, err={a['forecast_error']:.3f}")
        
        # Save anomalies
        existing = {}
        if os.path.exists(ANOMALIES_JSON_PATH):
            try:
                with open(ANOMALIES_JSON_PATH, "r") as f:
                    existing = json.load(f)
            except Exception:
                existing = {}
        existing[metric] = anomalies
        with open(ANOMALIES_JSON_PATH, "w") as f:
            json.dump(existing, f, indent=2)
        
        # Visualize results
        y_test_inv = scaler.inverse_transform(y_test)
        y_pred_inv = scaler.inverse_transform(y_pred)
        ts = pd.to_datetime(test_timestamps)[SEQUENCE_LENGTH:]
        
        plt.figure(figsize=(14, 6))
        plt.plot(ts, y_test_inv, label="Actual", linewidth=2)
        plt.plot(ts, y_pred_inv, label="Predicted", linestyle="--", linewidth=2)
        plt.scatter(ts[flags], y_test_inv[flags], color="red", label="Anomalies", s=50, edgecolors="black")
        plt.title(f"{metric} - Forecasting Anomalies")
        plt.xlabel("Time")
        plt.ylabel("Value")
        plt.legend()
        plt.grid(alpha=0.3)
        plt.tight_layout()
        plt.savefig(os.path.join(VISUALS_DIR, f"{metric.replace('.', '_')}_forecast_anomalies.png"))
        plt.close()
        
        # Clean up to free memory
        del model, scaler
        gc.collect()
        tf.keras.backend.clear_session()
        
    except Exception as e:
        print(f"[ERROR] Error on {metric}: {e}")

# Calculate and print overall MSE
if all_mse_values:
    overall_mse = np.mean(all_mse_values)
    print("\n===== MSE SCORES =====")
    for metric, mse in sorted(metric_mse_scores.items()):
        print(f"{metric}: {mse:.6f}")
    print(f"\nOVERALL MSE: {overall_mse:.6f}")
else:
    print("[WARN] No metrics were successfully processed. Cannot calculate MSE scores.")

print("[DONE] All metrics processed.")

2025-04-19 13:03:00.011794: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1745067780.208006      31 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1745067780.264261      31 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


[INFO] Found 273 unique metrics.
[INFO] Processing: redis.clients.blocked
[INFO] 'redis.clients.blocked' not trending (slope=0.0000)


I0000 00:00:1745067793.274538      31 gpu_device.cc:2022] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 15513 MB memory:  -> device: 0, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:04.0, compute capability: 6.0
I0000 00:00:1745067796.517603      90 service.cc:148] XLA service 0x7a05c8055aa0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
I0000 00:00:1745067796.518132      90 service.cc:156]   StreamExecutor device (0): Tesla P100-PCIE-16GB, Compute Capability 6.0
I0000 00:00:1745067796.811634      90 cuda_dnn.cc:529] Loaded cuDNN version 90300
I0000 00:00:1745067797.557718      90 device_compiler.h:188] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 52ms/step
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 78ms/step
[INFO] MSE for redis.clients.blocked: 0.000000
[INFO] Processing: redis.clients.connected
[INFO] 'redis.clients.connected' not trending (slope=0.0000)
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 43ms/step
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 71ms/step
[INFO] MSE for redis.clients.connected: 0.000000
[INFO] Processing: redis.clients.max_input_buffer
[INFO] 'redis.clients.max_input_buffer' not trending (slope=-19.8226)
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 43ms/step
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 61ms/step
[INFO] MSE for redis.clients.max_input_buffer: 1.332262
[INFO] Processing: redis.clients.max_output_buffer
[INFO] 'redis.clients.max_output_buffer' not trending (slope=0.0000)
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 47ms/step
4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
[INFO] MSE for redis.clients.max_output_buffer: 0.000000
[INFO] Processing: redis.commands
[INFO] 'redis.commands' not trending (slope=0.0026)
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 44ms/step
4/4 ━━━━━

## ARIMA

In [4]:
import os
import json
import pickle
import gc
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import tensorflow as tf
from statsmodels.tsa.arima.model import ARIMA
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error
from datetime import datetime
from zoneinfo import ZoneInfo
from multiprocessing import Process, set_start_method

# -------------------- Configuration --------------------

METRIC_DATASET_PATH = "/kaggle/working/metric_backup.json"
MODEL_DIR = "/kaggle/working/saved_models_lstm3"
VISUALS_DIR = "/kaggle/working/visuals_lstm3"
ANOMALIES_JSON_PATH = "/kaggle/working/anomalies3.json"

for folder in [MODEL_DIR, VISUALS_DIR]:
    os.makedirs(folder, exist_ok=True)

SEQUENCE_LENGTH = 30  # Used for consistency with original code
MIN_SAMPLES = 100
TRAIN_RATIO = 0.7
THRESHOLD_SIGMA = 6.0
TRENDING_SLOPE_THRESHOLD = 0.01

# ARIMA parameters
AR_ORDER = 5    # p parameter
DIFF_ORDER = 1  # d parameter
MA_ORDER = 0    # q parameter

# -------------------- Main Code (No Functions) --------------------

try:
    set_start_method("spawn")
except RuntimeError:
    pass

# Load dataset
df = pd.read_json(METRIC_DATASET_PATH, lines=True)
metrics = df["metric_name"].unique()
print(f"[INFO] Found {len(metrics)} unique metrics.")

# Prepare for MSE storage
metric_mse_scores = {}
overall_y_true = []
overall_y_pred = []

# Process each metric
for metric in metrics:
    print(f"[INFO] Processing: {metric}")
    
    metric_df = df[df["metric_name"] == metric].copy()
    metric_df["timestamp"] = pd.to_datetime(metric_df["timestamp"])
    metric_df.sort_values("timestamp", inplace=True)
    data = metric_df["value"].values.astype(float)
    timestamps = metric_df["timestamp"].values
    
    if len(data) == 0:
        print(f"[WARN] No data for '{metric}'. Skipping.")
        continue
    
    if len(data) < MIN_SAMPLES:
        print(f"[WARN] Not enough data for '{metric}' ({len(data)} < {MIN_SAMPLES}). Skipping.")
        continue
    
    x = np.arange(len(data))
    slope = np.polyfit(x, data, 1)[0]
    use_transformation = slope > TRENDING_SLOPE_THRESHOLD
    print(f"[INFO] '{metric}' {'trending' if use_transformation else 'not trending'} (slope={slope:.4f})")
    
    if use_transformation:
        diff = np.diff(data, prepend=data[0])
        data = np.where(diff < 0, 0, diff)
    
    split_idx = int(len(data) * TRAIN_RATIO)
    train_data = data[:split_idx]
    test_data = data[split_idx:]
    train_timestamps = timestamps[:split_idx]
    test_timestamps = timestamps[split_idx:]
    
    scaler = StandardScaler()
    train_scaled = scaler.fit_transform(train_data.reshape(-1, 1)).flatten()
    
    # ARIMA model instead of LSTM
    try:
        # Fit ARIMA model on training data
        model = ARIMA(train_scaled, order=(AR_ORDER, DIFF_ORDER, MA_ORDER))
        model_fit = model.fit()
        
        # Make one-step forecasts for training data
        history = train_scaled.tolist()
        y_pred_train = []
        
        # Get in-sample predictions for threshold calculation
        residuals = model_fit.resid
        mean_err, std_err = np.mean(np.abs(residuals)), np.std(np.abs(residuals))
        threshold = mean_err + THRESHOLD_SIGMA * std_err
        
        # Save model parameters and threshold
        with open(os.path.join(MODEL_DIR, f"{metric}_forecast.pkl"), "wb") as f:
            pickle.dump(model_fit, f)
        with open(os.path.join(MODEL_DIR, f"{metric}_scaler.pkl"), "wb") as f:
            pickle.dump(scaler, f)
        with open(os.path.join(MODEL_DIR, f"{metric}_thresholds.pkl"), "wb") as f:
            pickle.dump({
                "threshold": threshold,
                "mean_error": float(mean_err),
                "std_error": float(std_err),
                "use_transformation": use_transformation,
                "arima_order": (AR_ORDER, DIFF_ORDER, MA_ORDER)
            }, f)
        
        # Forecast for test data
        test_scaled = scaler.transform(test_data.reshape(-1, 1)).flatten()
        
        # For ARIMA we'll use a rolling forecast approach
        history = train_scaled.tolist()
        y_pred = []
        
        # Forecast one step at a time
        for i in range(len(test_scaled)):
            # Fit model on current history
            model = ARIMA(history, order=(AR_ORDER, DIFF_ORDER, MA_ORDER))
            model_fit = model.fit()
            
            # Make one-step forecast
            output = model_fit.forecast(steps=1)
            y_pred.append(output[0])
            
            # Update history with actual value
            history.append(test_scaled[i])
        
        y_pred = np.array(y_pred)
        y_test = test_scaled
        
        # Calculate errors
        errors = np.abs(y_test - y_pred)
        flags = errors > threshold
        
        # Calculate and log MSE for the current metric
        mse = mean_squared_error(y_test, y_pred)
        print(f"[MSE] {metric}: {mse:.6f}")
        metric_mse_scores[metric] = mse
        overall_y_true.append(y_test)
        overall_y_pred.append(y_pred)
        
        anomalies = []
        for i, flag in enumerate(flags):
            if flag:
                anomalies.append({
                    "timestamp": pd.to_datetime(test_timestamps[i]).isoformat(),
                    "value": float(test_data[i]),
                    "forecast_error": float(errors[i])
                })
        
        for a in anomalies:
            print(f"[ANOMALY] {metric} @ {a['timestamp']}: val={a['value']:.3f}, err={a['forecast_error']:.3f}")
        
        existing = {}
        if os.path.exists(ANOMALIES_JSON_PATH):
            try:
                with open(ANOMALIES_JSON_PATH, "r") as f:
                    existing = json.load(f)
            except Exception:
                existing = {}
        existing[metric] = anomalies
        with open(ANOMALIES_JSON_PATH, "w") as f:
            json.dump(existing, f, indent=2)
        
        y_test_inv = scaler.inverse_transform(y_test.reshape(-1, 1))
        y_pred_inv = scaler.inverse_transform(y_pred.reshape(-1, 1))
        ts = pd.to_datetime(test_timestamps)
        
        plt.figure(figsize=(14, 6))
        plt.plot(ts, y_test_inv, label="Actual", linewidth=2)
        plt.plot(ts, y_pred_inv, label="Predicted", linestyle="--", linewidth=2)
        plt.scatter(ts[flags], y_test_inv[flags], color="red", label="Anomalies", s=50, edgecolors="black")
        plt.title(f"{metric} - Forecasting Anomalies")
        plt.xlabel("Time")
        plt.ylabel("Value")
        plt.legend()
        plt.grid(alpha=0.3)
        plt.tight_layout()
        plt.savefig(os.path.join(VISUALS_DIR, f"{metric.replace('.', '_')}_forecast_anomalies.png"))
        plt.close()
        
    except Exception as e:
        print(f"[ERROR] Failed to process '{metric}': {str(e)}")
        continue
    
    del model, scaler
    gc.collect()

# Calculate and print overall MSE
if overall_y_true and overall_y_pred:
    all_true = np.concatenate(overall_y_true)
    all_pred = np.concatenate(overall_y_pred)
    overall_mse = mean_squared_error(all_true, all_pred)
    print(f"\n[OVERALL MSE] Across all metrics: {overall_mse:.6f}")

print("[DONE] All metrics processed.")

[INFO] Found 273 unique metrics.
[INFO] Processing: redis.clients.blocked
[INFO] 'redis.clients.blocked' not trending (slope=0.0000)


/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood op

[MSE] redis.clients.blocked: 0.000000
[INFO] Processing: redis.clients.connected
[INFO] 'redis.clients.connected' not trending (slope=0.0000)


/usr/local/lib/python3.11/dist-packages/scipy/optimize/_numdiff.py:596: RuntimeWarning: invalid value encountered in subtract
  df = fun(x1) - f0


[MSE] redis.clients.connected: 0.000000
[INFO] Processing: redis.clients.max_input_buffer
[INFO] 'redis.clients.max_input_buffer' not trending (slope=-19.8226)
[MSE] redis.clients.max_input_buffer: 1.060148
[INFO] Processing: redis.clients.max_output_buffer
[INFO] 'redis.clients.max_output_buffer' not trending (slope=0.0000)


...

[MSE] kafka.request.queue: 0.000000
[INFO] Processing: kafka.controller.active.count
[INFO] 'kafka.controller.active.count' not trending (slope=0.0000)


/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood op

[MSE] kafka.controller.active.count: 0.000000
[INFO] Processing: kafka.purgatory.size
[INFO] 'kafka.purgatory.size' trending (slope=0.0203)
[MSE] kafka.purgatory.size: 1.015488
[INFO] Processing: kafka.logs.flush.time.50p
[INFO] 'kafka.logs.flush.time.50p' not trending (slope=0.0000)


/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood op

[MSE] kafka.logs.flush.time.50p: 0.000000
[INFO] Processing: kafka.request.time.total
[INFO] 'kafka.request.time.total' trending (slope=153.7917)
[MSE] kafka.request.time.total: 0.567785
[ANOMALY] kafka.request.time.total @ 2025-04-09T11:23:00: val=0.000, err=8.950
[INFO] Processing: http.client.connection.duration
[INFO] 'http.client.connection.duration' trending (slope=0.2006)
[MSE] http.client.connection.duration: 1.708683
[ANOMALY] http.client.connection.duration @ 2025-04-09T11:24:00: val=9.000, err=9.883
[INFO] Processing: otelcol_processor_batch_timeout_trigger_send
[INFO] 'otelcol_processor_batch_timeout_trigger_send' trending (slope=0.3732)
[MSE] otelcol_processor_batch_timeout_trigger_send: 1.251907
[ANOMALY] otelcol_processor_batch_timeout_trigger_send @ 2025-04-03T12:12:00: val=2.000, err=3.428
[INFO] Processing: system.paging.usage
[WARN] Not enough data for 'system.paging.usage' (1 < 100). Skipping.
[INFO] Processing: app.currency_counter
[WARN] Not enough data for 'app.c

## SARIMA

In [2]:
import os
import json
import pickle
import gc
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from statsmodels.tsa.statespace.sarimax import SARIMAX
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error
from datetime import datetime
from zoneinfo import ZoneInfo
from multiprocessing import Process, set_start_method

# -------------------- Configuration --------------------

METRIC_DATASET_PATH = "/kaggle/working/metric_backup.json"
MODEL_DIR = "/kaggle/working/saved_models"
VISUALS_DIR = "/kaggle/working/visuals"
ANOMALIES_JSON_PATH = "/kaggle/working/anomalies.json"

for folder in [MODEL_DIR, VISUALS_DIR]:
    os.makedirs(folder, exist_ok=True)

SEQUENCE_LENGTH = 30  # Still using this for context window
MIN_SAMPLES = 100
TRAIN_RATIO = 0.7
THRESHOLD_SIGMA = 6.0
TRENDING_SLOPE_THRESHOLD = 0.01

# SARIMA specific parameters
ORDER = (1, 1, 1)  # (p, d, q) - non-seasonal part
SEASONAL_ORDER = (1, 1, 1, 12)  # (P, D, Q, s) - seasonal part

# Dictionary to store MSE scores
metric_mse_scores = {}
all_mse_values = []

try:
    set_start_method("spawn")
except RuntimeError:
    pass

# Load the dataset
df = pd.read_json(METRIC_DATASET_PATH, lines=True)
metrics = df["metric_name"].unique()
print(f"[INFO] Found {len(metrics)} unique metrics.")

# Process each metric
for metric in metrics:
    try:
        print(f"[INFO] Processing: {metric}")
        
        # Filter and sort data for the current metric
        metric_df = df[df["metric_name"] == metric].copy()
        metric_df["timestamp"] = pd.to_datetime(metric_df["timestamp"])
        metric_df.sort_values("timestamp", inplace=True)
        data = metric_df["value"].values.astype(float)
        timestamps = metric_df["timestamp"].values
        
        if len(data) == 0:
            print(f"[WARN] No data for '{metric}'. Skipping.")
            continue
            
        if len(data) < MIN_SAMPLES:
            print(f"[WARN] Not enough data for '{metric}' ({len(data)} < {MIN_SAMPLES}). Skipping.")
            continue
            
        # Check if the metric is trending
        x = np.arange(len(data))
        slope = np.polyfit(x, data, 1)[0]
        use_transformation = slope > TRENDING_SLOPE_THRESHOLD
        print(f"[INFO] '{metric}' {'trending' if use_transformation else 'not trending'} (slope={slope:.4f})")
        
        # Transform data if needed
        if use_transformation:
            # Calculate differences and clip negative values
            diff = np.diff(data, prepend=data[0])
            data = np.where(diff < 0, 0, diff)
        
        # Split into train and test sets
        split_idx = int(len(data) * TRAIN_RATIO)
        train_data, test_data = data[:split_idx], data[split_idx:]
        train_timestamps, test_timestamps = timestamps[:split_idx], timestamps[split_idx:]
        
        # Scale the data
        scaler = StandardScaler()
        train_scaled = scaler.fit_transform(train_data.reshape(-1, 1)).flatten()
        
        # Create a pandas Series with time index for SARIMA
        train_series = pd.Series(train_scaled, index=pd.DatetimeIndex(train_timestamps))
        
        # Build and train the SARIMA model
        model = SARIMAX(
            train_series,
            order=ORDER,
            seasonal_order=SEASONAL_ORDER,
            enforce_stationarity=False,
            enforce_invertibility=False
        )
        
        model_fit = model.fit(disp=False)
        
        # Get in-sample predictions for the training data
        y_train = train_scaled[SEQUENCE_LENGTH:]
        y_pred_train = model_fit.predict(start=SEQUENCE_LENGTH, end=len(train_scaled)-1)
        
        # Compute errors on training data
        errors = np.abs(y_train - y_pred_train)
        mean_err, std_err = np.mean(errors), np.std(errors)
        threshold = mean_err + THRESHOLD_SIGMA * std_err
        
        # Save model and related data
        with open(os.path.join(MODEL_DIR, f"{metric}_forecast.pkl"), "wb") as f:
            pickle.dump(model_fit, f)
        with open(os.path.join(MODEL_DIR, f"{metric}_scaler.pkl"), "wb") as f:
            pickle.dump(scaler, f)
        with open(os.path.join(MODEL_DIR, f"{metric}_thresholds.pkl"), "wb") as f:
            pickle.dump({
                "threshold": threshold,
                "mean_error": float(mean_err),
                "std_error": float(std_err),
                "use_transformation": use_transformation
            }, f)
        
        # Detect anomalies in test data
        if use_transformation:
            diff = np.diff(test_data, prepend=test_data[0])
            test_data = np.where(diff < 0, 0, diff)
            
        test_scaled = scaler.transform(test_data.reshape(-1, 1)).flatten()
        
        # Use the model to forecast the test data
        test_series = pd.Series(test_scaled, index=pd.DatetimeIndex(test_timestamps))
        
        # Create full series for prediction
        full_series = pd.concat([train_series, test_series])
        
        # Forecast test values
        y_test = test_scaled[SEQUENCE_LENGTH:]
        test_timestamps_seq = test_timestamps[SEQUENCE_LENGTH:]
        
        if len(y_test) == 0:
            print(f"[WARN] Insufficient sequence data for '{metric}'.")
            continue
        
        # Make predictions on test data
        y_pred = model_fit.forecast(len(y_test))
        
        # Calculate MSE for this metric
        mse = mean_squared_error(y_test, y_pred)
        metric_mse_scores[metric] = mse
        all_mse_values.append(mse)
        print(f"[INFO] MSE for {metric}: {mse:.6f}")
        
        # Calculate errors and find anomalies
        errors = np.abs(y_test - y_pred)
        flags = errors > threshold
        
        # Collect anomalies
        anomalies = []
        for i, flag in enumerate(flags):
            if flag:
                idx = i + SEQUENCE_LENGTH
                if idx < len(test_timestamps):
                    anomalies.append({
                        "timestamp": pd.to_datetime(test_timestamps[idx]).isoformat(),
                        "value": float(test_data[idx]),
                        "forecast_error": float(errors[i])
                    })
        
        # Print anomalies
        for a in anomalies:
            print(f"[ANOMALY] {metric} @ {a['timestamp']}: val={a['value']:.3f}, err={a['forecast_error']:.3f}")
        
        # Save anomalies
        existing = {}
        if os.path.exists(ANOMALIES_JSON_PATH):
            try:
                with open(ANOMALIES_JSON_PATH, "r") as f:
                    existing = json.load(f)
            except Exception:
                existing = {}
        existing[metric] = anomalies
        with open(ANOMALIES_JSON_PATH, "w") as f:
            json.dump(existing, f, indent=2)
        
        # Visualize results
        y_test_inv = scaler.inverse_transform(y_test.reshape(-1, 1)).flatten()
        y_pred_inv = scaler.inverse_transform(y_pred.reshape(-1, 1)).flatten()
        ts = pd.to_datetime(test_timestamps_seq)
        
        plt.figure(figsize=(14, 6))
        plt.plot(ts, y_test_inv, label="Actual", linewidth=2)
        plt.plot(ts, y_pred_inv, label="Predicted", linestyle="--", linewidth=2)
        plt.scatter(ts[flags], y_test_inv[flags], color="red", label="Anomalies", s=50, edgecolors="black")
        plt.title(f"{metric} - Forecasting Anomalies")
        plt.xlabel("Time")
        plt.ylabel("Value")
        plt.legend()
        plt.grid(alpha=0.3)
        plt.tight_layout()
        plt.savefig(os.path.join(VISUALS_DIR, f"{metric.replace('.', '_')}_forecast_anomalies.png"))
        plt.close()
        
        # Clean up to free memory
        del model_fit, scaler
        gc.collect()
        
    except Exception as e:
        print(f"[ERROR] Error on {metric}: {e}")

# Calculate and print overall MSE
if all_mse_values:
    overall_mse = np.mean(all_mse_values)
    print("\n===== MSE SCORES =====")
    for metric, mse in sorted(metric_mse_scores.items()):
        print(f"{metric}: {mse:.6f}")
    print(f"\nOVERALL MSE: {overall_mse:.6f}")
else:
    print("[WARN] No metrics were successfully processed. Cannot calculate MSE scores.")

print("[DONE] All metrics processed.")

[INFO] Found 273 unique metrics.
[INFO] Processing: redis.clients.blocked
[INFO] 'redis.clients.blocked' not trending (slope=0.0000)


/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:837: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:837: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/

[INFO] MSE for redis.clients.blocked: 0.000000
[ERROR] Error on redis.clients.blocked: 'Series' object has no attribute 'reshape'
[INFO] Processing: redis.clients.connected
[INFO] 'redis.clients.connected' not trending (slope=0.0000)


/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:837: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:837: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)


[INFO] MSE for redis.clients.connected: 0.040220
[ERROR] Error on redis.clients.connected: 'Series' object has no attribute 'reshape'
[INFO] Processing: redis.clients.max_input_buffer
[INFO] 'redis.clients.max_input_buffer' not trending (slope=-19.8226)


...

[INFO] MSE for kafka.logs.flush.time.50p: 0.000000
[ERROR] Error on kafka.logs.flush.time.50p: 'Series' object has no attribute 'reshape'
[INFO] Processing: kafka.request.time.total
[INFO] 'kafka.request.time.total' trending (slope=153.7917)


/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:837: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:837: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)


[INFO] MSE for kafka.request.time.total: 81.002005
[ERROR] Error on kafka.request.time.total: 0
[INFO] Processing: http.client.connection.duration
[INFO] 'http.client.connection.duration' trending (slope=0.2006)


/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:837: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:837: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency min will be used.
  self._init_dates(dates, freq)
/usr/local/lib/python3.11/dist-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: No frequency information was provided, so inferred frequency min will be used.
  self._init_dates(dates, freq)


[INFO] MSE for http.client.connection.duration: 1.367500
[ERROR] Error on http.client.connection.duration: 110
[INFO] Processing: otelcol_processor_batch_timeout_trigger_send
[INFO] 'otelcol_processor_batch_timeout_trigger_send' trending (slope=0.3732)
[INFO] MSE for otelcol_processor_batch_timeout_trigger_send: 4.438055
[ERROR] Error on otelcol_processor_batch_timeout_trigger_send: 'Series' object has no attribute 'reshape'
[INFO] Processing: system.paging.usage
[WARN] Not enough data for 'system.paging.usage' (1 < 100). Skipping.
[INFO] Processing: app.currency_counter
[WARN] Not enough data for 'app.currency_counter' (1 < 100). Skipping.

===== MSE SCORES =====
app.ads.ad_requests: 2.286082
container.blockio.io_service_bytes_recursive: 0.020332
container.cpu.usage.kernelmode: 0.439357
container.cpu.usage.total: 0.762317
container.cpu.usage.usermode: 0.909074
container.cpu.utilization: 0.000000
container.memory.file: 0.424901
container.memory.percent: 0.000000
container.memory.usage.